# Download and merge point clouds

This notebook will create a LAS dataset from a folder of LAZ files. It will also colorize the point cloud from an RGB image from the ImageServices service hosted on the KyRaster.Ky.gov ArcGIS Server.

It will create a merged LAS file that can be uploaded to 3D mapping platforms.

In [ ]:
############### Modules and Functions :: DO NOT EDIT ###############

# Import ArcGIS package
import arcpy
# Subprocess allows us to issue commands on the command line
import subprocess
# Zip utlity to extract files
from zipfile import ZipFile
# Get current local time
import datetime

# Allow overwriting of existing data
arcpy.env.overwriteOutput = True

############### Utility functions ###############

def setWork():
    """Create dictionary of path names from global variables 
    and return dot.notation access to dictionary attributes.
    Used internally for shorthand access to path names."""
    class dotdict(dict):
        """dot.notation"""
        __getattr__ = dict.get
        __setattr__ = dict.__setitem__
        __delattr__ = dict.__delitem__
    p = {
        "project": f'{root}\\{folder}',
        "db": f'{root}\\{folder}\\{folder}.gdb',
        "lidar": f'{root}\\{folder}\\lidar',
        "download": f'{root}\\{folder}\\download',
        "laz": f"{root}\\tools\\LAStools\\bin\\laszip64.exe",
        "lasmerge": f"{root}\\tools\\LAStools\\bin\\lasmerge64.exe",
        "grid":  f"{root}\\tools\\grids\\Phase1.gdb\\KY_5k_LAZ",
        "lasd": f'{root}\\{folder}\\download\\combined.lasd',
        "lasdaoi": f'{root}\\{folder}\\download\\aoi_e.lasd',
        "aoi": f'{root}\\{folder}\\lidar\\aoi.lasd',
        "bands": 'RED Band_1; GREEN Band_2; BLUE Band_3',
        "img": "ImageServices\\Ky_NAIP_2020_2ft",
        "dsm": f'{root}\\{folder}\\lidar\\dsm.lasd',
    }
    return dotdict(p)

def listContents(root, folder):
    """Function to print contents of a directory and report time when the cell finished processing.
    listContents(root, folder)
    Two arguments:
        root = drive letter and folder for your root GIS space (string)
        folder = path to folder in root (string)
    """
    downloads = f'{root}\\{folder}'
    completed = subprocess.run(f'dir {downloads}', shell=True, stdout=subprocess.PIPE)
    print(completed.stdout.decode('UTF-8'))
    print("Finished processing", datetime.datetime.now())

def checkFolder(name):
    """Function to check folder name against special characters for creating project space.
    checkFolder(name)
    One argument:
        name = name of project folder for this application (string)
    """
    special = "\"\' :;\\.!@#$%^&*()-+?=,<>/"
    if any(letter in special for letter in name):
        print("Whoops! You have a special character in your project's name. \nPlease change project name.")
        return False
    else:
        print(f'Creating your project folder...')
        return True
    
############### Project Functions :: DO NOT EDIT ###############

def setUpProject():
    """Function to create project folder and database in root GIS.
    setUpProject()
    No arguments
    """
    p = setWork()
    if checkFolder(folder):
        subprocess.run(f'mkdir {p.project}', shell=True)
        subprocess.run(f'mkdir {p.download}', shell=True)
        subprocess.run(f'mkdir {p.lidar}', shell=True)
        print(f'Your project has been created in the {p.project} folder')
    # Create project geodatabase
    if arcpy.Exists(p.db):
        print(f'{p.db} exists!')
    else:
        print(f"Creating {p.db}")
        arcpy.CreateFileGDB_management(p.project, folder)
    arcpy.env.workspace = p.db
            
def setAoi(lat, lon, buffer):
    """Function to create area of interest and clip LAZ grid layer 
    to interactively download LAZ files.
    setAoi(lat, lon, buffer)
    Three arguments:
        lat = latitude for center of AOI (number)
        lon = longitude for center of AOI (number)
        buffer = distance, in feet, from center of AOI to include in analysis (number)
    """
    p = setWork()
    ky = arcpy.SpatialReference(3089)
    wgs84 = arcpy.SpatialReference(4326)
    arcpy.env.workspace = p.db
    point = arcpy.Point(lon, lat) 
    ptGeometry = arcpy.PointGeometry(point, wgs84)
    arcpy.env.outputCoordinateSystem = ky
    arcpy.CopyFeatures_management(ptGeometry, "point")
    arcpy.analysis.Buffer("point", "aoi", buffer)
    arcpy.analysis.Clip(p.grid, "aoi", "laz_grid")
    
def processLaz():
    """Function to convert LAZ file to a LAS dataset and extract AOI point cloud.
    processLaz()
    No arguments
    Note: This functions produce duplicate LAS for the AOI dataset. 
    """
    p = setWork()
    ky = arcpy.SpatialReference(3089)
    arcpy.env.workspace = p.db
    las_tools = p.laz
    las = []
    subprocess.run(f'dir {p.download}\\*.laz /b > {p.download}\\zips.txt', shell=True, stdout=subprocess.PIPE)
    with open(f'{p.download}\\zips.txt', 'r') as fileList:
        for line in fileList:
            name = line.strip()
            subprocess.run(f'{las_tools} -i {p.download}\\{name} -o {p.download}\\{name[:-4]}.las', shell=True, stdout=subprocess.PIPE)
            las.append(f'{p.download}\\{name[:-4]}.las')
    arcpy.CreateLasDataset_management (las, p.lasd, "#", "#", ky, True, True)
    arcpy.ExtractLas_3d (p.lasd, p.download, "#", 'aoi',  "#", "_e", "#", "#", True, p.lasdaoi)
        
# Function to unzip downloaded files  
def colorizeWith(image):
    """Function to add color attributes to LAS files from ImageServices RGB image.
    colorizeWith(image)
    One argument:
    image = name of KyRaster ImageServices RGB layer you want use to colorize point cloud (string)
    """
    p = setWork()
    ky = arcpy.SpatialReference(3089)
    arcpy.env.workspace = p.db
    arcpy.ColorizeLas_3d (p.lasdaoi, image, p.bands, p.lidar, f"_{image}", "#", "#","#", "#", True, p.aoi)
                
# Function to unzip downloaded files  
def shade(classcodes, name):
    """Function to create raster elevation and shaded relief models from AOI LAS dataset.
    shade(classcodes, name)
    Two arguments:
        classcodes = LAS class codes used to filter input point cloud (list of integers)
        name = name of output layers (string)
    """
    p = setWork()
    arcpy.MakeLasDatasetLayer_management (p.aoi, p.dsm, classcodes)
    arcpy.LasDatasetToRaster_conversion (p.dsm, name, "#", "#", "#", "#", 5)
    arcpy.HillShade_3d(name, f'{name}_hillshade', 270, 55)
    
# Function to create project space in root GIS       
def cleanUp():
    """Delete all LAS and LASD files in download folder.
    cleanUp()
    No arguments
    Note: Make sure final aoi LAS files are saved in the lidar folder. LAZ files are not deleted. 
    """
    select = input(f"Do you want to delete LAS files in downloads folder? Yes or No ")
    p = setWork()
    if 'y' in select.lower():
        subprocess.run(f'dir {p.download}\\*.las* /b /s > {p.download}\\del.txt', shell=True)
        with open(f'{p.download}\\del.txt', 'r') as fileList:
            for line in fileList:
                subprocess.run(f'del {line.strip()}', shell=True)
        print(f'All gone!')


# Function to unzip downloaded files  
def copyColorlasd(image):
    """Create a copy of the AOI LASD and LAS files in the lidar folder and append image name to the file names.
    Used when a new colorized LASD is desired.
    colorizeWith(image)
    One argument:
    image = name of RGB layer you want use append to LAS file names (string)
    """
    p = setWork()
    ky = arcpy.SpatialReference(3089)
    arcpy.env.workspace = p.db
    las = []
    subprocess.run(f'dir {p.lidar}\\*{image}.las /b > {p.lidar}\\img.txt', shell=True, stdout=subprocess.PIPE)
    with open(f'{p.lidar}\\img.txt', 'r') as fileList:
        for line in fileList:
            name = line.strip()
            las.append(f'{p.lidar}\\{name}')
            print(las)
    arcpy.CreateLasDataset_management (las, f'{p.lidar}\\aoi_{image}.lasd', "#", "#", ky, True, True)
    
# Function to unzip downloaded files  
def mergeLAS():
    """Function run command line tool LASTools to merge LAS files into a single file. Useful for web mapping platforms.
    mergeLAS()
    No arguments
    """
    p = setWork()
    las = p.lidar
    
    print('Command line command that will be executed:')
    print(f'dir {las}\\"*_*.las" /b /s > {las}\\las.txt')
    completed = subprocess.run(f'dir {las}\\"*_*.las" /b /s > {las}\\las.txt', shell=True, stdout=subprocess.PIPE)
    print('Command line command that will be executed:')
    print(f"{p.lasmerge} -lof {las}\\las.txt -drop_class 7 18 -o {las}\\{folder}.las")
    subprocess.run(f"{p.lasmerge} -lof {las}\\las.txt -drop_class 7 18 -o {las}\\{folder}.las")


## Before you start
* Have a root GIS folder on your C: Drive.
* Either run the *START_HERE.ipynb* to set up your environment, or download and extract [tools](https://nyc3.digitaloceanspaces.com/astoria/geo409/start/tools.zip) folder into your root GIS space.
* Insert a New Local Scene into ArcGIS Pro.

![Insert a New Local Scene into ArcGIS Pro](https://nyc3.digitaloceanspaces.com/astoria/geo409/images/new-local-scene.jpg)   
*Inserting a New Local Scene into ArcGIS Pro*

In [ ]:
############### Global variables :: EDIT for your AOI ###############

# Directory path to your root GIS folder. 
root = "c:\\YodasGIS"

# Project name - creates a folder in your root GIS directory.
folder = "NolinRiverDam"

# Where is your Area of Interest in Kentucky?
lat = 37.2771333
lon = -86.2468067

# How far in feet from the above point do you want to process lidar data?
buffer = 2000

# What RGB image from the KyRaster Image Services are you using?
# Look in the Catalog > Servers > services on kyraster > ImageServices for exact name
image = "Ky_NAIP_2020_2FT"

In [ ]:
setUpProject()

In [ ]:
setAoi(lat, lon, buffer)

## Download LAZ files

Instructions

1. Verify a new layer called *laz_grid* is in your content pane. If not, add it to your scene from the project's geodatabase.
2. Click on each tile in the layer. Click on *download_url* and save them to your project's *download* folder.


In [ ]:
# Let's see if you LAZ files in your project's download folder
listContents(root, f'{folder}\\download')

In [ ]:
# Extract AOI from combined LASD
# Remove the aoi_e.lasd and combinded.lasd from scene or map
processLaz()

In [ ]:
# Load NAIP imagery
#
a = f'https://kyraster.ky.gov/arcgis/rest/services/ImageServices/{image}/ImageServer'
b = arcpy.sa.Raster(a)

# Verify
b

In [ ]:
# Extract area of interest
#
c = arcpy.sa.ExtractByMask(b, 'aoi')

# Save it to the geodatabase
c.save('naip')

# Verify
c

In [ ]:
# Colorize point cloud and output new aoi.lasd. Use this file for visualization.
#
colorizeWith('naip')

In [ ]:
# Merge las files into single file for upload to mapping platforms
#
mergeLAS()
print("Look in the project's lidar folder to find the merged LAS file. Use this for uploads.")

In [ ]:
# Delete the downloads folder
#
cleanUp()